# Week 05: Continuing interactivity in Python with the viz engine bqplot

### A bit with traitlets

Remember our color-picker that we linked:

In [22]:
import ipywidgets

In [23]:
islider = ipywidgets.IntSlider(min = 0, max = 10, step = 1, orientation = 'vertical')
islider

IntSlider(value=0, max=10, orientation='vertical')

In [24]:
cp = ipywidgets.ColorPicker()
cp

ColorPicker(value='black')

Let's link them using .link this time:

In [25]:
ipywidgets.link( (cp, 'value'), (islider.style, 'handle_color') )

We note what prints out now is a "traitlets.traitlets" link -- this is part of the python-backend traitlets library.

Traitlets are a way to link the *change in a variable* to an action.

We'll start by making a class w/o using traitlets.  We've worked with classes before, just sort of "under the radar" like with Pandas objects.  Now we will define our own:

In [1]:
class MyObject():
    name = 'unnamed'
    age = 0

Let's define a new variable of this `class` type:

In [2]:
my_obj = MyObject()

In [3]:
my_obj.name, my_obj.age

('unnamed', 0)

We can update the values of these variables like we would any other object:

In [4]:
my_obj.name = 'Bob'; my_obj.age = 47

Now, let's check out our new values:

In [5]:
print('Hello, my name is:', my_obj.name, 'and I am', my_obj.age, 'years old')

Hello, my name is: Bob and I am 47 years old


Now, let's say I wanted to re-set the values of the variables in my class -- to print out the above statement, I'd have to redo everything:

In [6]:
my_obj.name = 'Linda'; my_obj.age = 45

In [7]:
print('Hello, my name is:', my_obj.name, 'and I am', my_obj.age, 'years old')

Hello, my name is: Linda and I am 45 years old


The `traitlets` library allows us to "track" changes so that we can associate actions with updates to variables.  Let's try this example again:

In [8]:
import traitlets

In [9]:
class MyTraitletObject(traitlets.HasTraits):
    # lets use the unicode trait to let our object have a name
    name = traitlets.Unicode("unnamed") 
    # lets also give our object an age
    age = traitlets.Int(0)

In [10]:
my_t_obj = MyTraitletObject()
my_t_obj.age = 47
my_t_obj.name = 'Bob'

In [11]:
print('Hello, my name is:', my_t_obj.name, 'and I am', my_t_obj.age, 'years old')

Hello, my name is: Bob and I am 47 years old


So far this is not very exciting - we are back where we started!  However, there are options to "observe" changes in our traits:

Let's create a function that can act on one of the variables of our variables, in particluar, its going to react to the name in my object:

In [12]:
def name_changed(change):
    print(change) # this is a format that is required of a traitlets class

# lets tell traitlets that we are going to change something
my_t_obj.observe(name_changed, ['name'])

In [13]:
my_t_obj.name = 'Linda'

{'name': 'name', 'old': 'Bob', 'new': 'Linda', 'owner': <__main__.MyTraitletObject object at 0x7f9c880220a0>, 'type': 'change'}


We can see that there are these weird "new" and "old" names -- this is tracking how things change. The "owner" is just pointing to the memory location of `my_t_obj`.

Let's do something a little more exciting - have a default print-out of the introduction:

In [14]:
def name_changed2(change):
    print('Hello, my name is', change['new'], 'and I am', change['owner'].age, 'years old')

# lets tell traitlets that we are going to change something
my_t_obj.observe(name_changed2, ['name'])

In [15]:
my_t_obj.name = 'Linda'

Note that now, I've got *2* things associated with any changes -- let's take off the first one:

In [16]:
my_t_obj.unobserve(name_changed, ['name'])

In [17]:
my_t_obj.name = "Bob"

Hello, my name is Bob and I am 47 years old


We can practice by making a "watching for a change" function for age as well:

In [18]:
def age_changed(change):
    print('Hello, my name is', change['owner'].name, 'and I am', change['new'], 'years old')

my_t_obj.observe(age_changed, ['age'])

In [19]:
my_t_obj.age = 48

Hello, my name is Bob and I am 48 years old


In [20]:
my_t_obj.name, my_t_obj.age = 'Louise', 8

Hello, my name is Louise and I am 48 years old
Hello, my name is Louise and I am 8 years old


## On to bqplot!

Make sure you have installed this via the install script `test_imports_week01.ipynb` in week 1.  You may have to restart your jupyter or your browswer.

We'll start by using `bqplot` in a Grammar of Graphics & *Declaritive* sort of way, and then, if we have time, spend a few moments looking at its `matplotlib`-like interface as well which is an *Imperative* method.

In [1]:
import bqplot
import numpy as np
import ipywidgets

Now we are going to mess around with some of the declaritive programming type options that bqplot can use.  This will rely heavily on the "Grammar of Graphics" constructs.

## Random line plot with Pan/Zoom interaction

We'll now go through the example I put up on the slides for this week. 

**Data:** Let's first start by creating *data* elements for our graphic just some random numbers:

In [2]:
x = np.arange(100) # integers 0->999
y = np.random.random(100) + 5 # random numbers with mean = 5

In [3]:
x, y

(array([ 0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16,
        17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33,
        34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50,
        51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67,
        68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84,
        85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99]),
 array([5.93661483, 5.34624955, 5.73513537, 5.23408942, 5.45306324,
        5.64365054, 5.33392401, 5.48639708, 5.91656965, 5.75897354,
        5.05339608, 5.94327334, 5.75273631, 5.46951423, 5.39720997,
        5.41478471, 5.46423287, 5.55338327, 5.47241503, 5.36191841,
        5.76432492, 5.57416212, 5.54412269, 5.96641869, 5.31596885,
        5.88124223, 5.6305342 , 5.18198671, 5.84524615, 5.09018105,
        5.69861928, 5.77510297, 5.78567191, 5.67110384, 5.07511995,
        5.14591443, 5.36716692, 5.3643783 , 5.13785008, 5.60991725,
      

**Scales:** Now we'll define some scale objects which will determine how lines will be drawn on our canvas:

In [4]:
bqplot.LinearScale?

In [5]:
x_sc = bqplot.LinearScale()
y_sc = bqplot.LinearScale()

**Marks:** Now we are going to use GoG type calls to define what lines to actually draw combining information about our data and our scales:

In [6]:
bqplot.Lines?

In [7]:
lines = bqplot.Lines(x = x, y = y, scales = {'x': x_sc, 'y': y_sc})

**Axis:** Now, we are going to define what axis we want placed around the lines that we draw we'll draw both x & y axis.

In [8]:
bqplot.Axis?

In [9]:
ax_x = bqplot.Axis(scale = x_sc, label = 'X Value')
ax_y = bqplot.Axis(scale = y_sc, label = 'Y Value', orientation = 'vertical')

**Figure:** Finally, we combine all these things together into a bonified figure:

In [10]:
bqplot.Figure?

In [11]:
fig = bqplot.Figure(marks = [lines], axes = [ax_x, ax_y])
#display(fig) # you might also want to try "display"
# if you don't see the following fig, here is where
#  you might have to close and reopen your notebook
fig # note: just "fig" instead of "display(fig)" may also be an option for you

Figure(axes=[Axis(label='X Value', scale=LinearScale(), side='bottom'), Axis(label='Y Value', orientation='ver…

Ok, but this isn't interactive in anyway lets make it!!  There are a few "interactions" supported in `bqplot` but not all of them are supported for all types of plots.  The docs can be a little nebulous about what plot can use what type of interaction, so we'll just try a few and see what happens.  Here, let's add in an ability to pan/zoom in our plot:

In [12]:
bqplot.interacts?

In [13]:
bqplot.interacts.PanZoom?

In [14]:
pz = bqplot.interacts.PanZoom( scales = {'x': [x_sc], 'y': [y_sc]})

In [15]:
fig = bqplot.Figure(marks = [lines], axes = [ax_x, ax_y], interaction = pz)
#display(fig)
fig

Figure(axes=[Axis(label='X Value', scale=LinearScale(), side='bottom'), Axis(label='Y Value', orientation='ver…

Note that if I pan and zoom, the figure updates. Ooooo. fancy.

Note also, that the above figure also reacts as well this is because we are using the same lines & ax's objects -- recall back to last week that this was a feature of using ipywidgets and traitlets as well.

### ASIDE: where things can go wrong (SKIPPING generally):

In [19]:
# lets see an example of where this can fail

# first lets make an x from 0-10 in 100 steps
x = np.mgrid[0.0:10.0:100j]
# and 2 y variables
y1 = x * 2
y2 = x**2

In [20]:
x_sc = bqplot.LinearScale(min = 1, max = 10)
# lets do one y-scale over linear and 1 over log
y_sc1 = bqplot.LinearScale(min = 1, max = 20)
y_sc2 = bqplot.LogScale(min = 1, max = 100)

In [21]:
# lets genrate lines for each y value
lines1 = bqplot.Lines(x = x, y = y1, scales = {'x': x_sc, 'y': y_sc1})
lines2 = bqplot.Lines(x = x, y = y2, scales = {'x': x_sc, 'y': y_sc2})

In [22]:
# and lets plot an x axis like before
ax_x = bqplot.Axis(scale = x_sc, label = 'X Value')
# and one y axis on the left
ax_y1 = bqplot.Axis(scale = y_sc1, label = 'Y1 Value', 
                    orientation = 'vertical')
# and one y-axis on the right
ax_y2 = bqplot.Axis(scale = y_sc2, label = 'Y2 Value', 
                    orientation = 'vertical', side = 'right')

In [23]:
# lets allow pan and zoom
pz = bqplot.interacts.PanZoom(scales = {'x': [x_sc], 
                                        'y': [y_sc1, y_sc2]})
#bqplot.interacts.PanZoom?
fig = bqplot.Figure(marks = [lines1, lines2], 
                    axes = [ax_x, ax_y1, ax_y2], interaction=pz)
#display(fig)
fig
# now we note if we zoom out too far, or pan to too negative of the x-axis
# we lose a line

# why? because the line is log-scaled, and log(numbers < 0) is undefined

# this is a way in which declaritive programming can fail because there
#  aren't obvious options to inhibit pan&zoom to a positive range

Figure(axes=[Axis(label='X Value', scale=LinearScale(max=10.0, min=1.0)), Axis(label='Y1 Value', orientation='…

### END ASIDE/SKIP

FYI lots of more fun notebooks here: https://github.com/dmadeka/PyGotham-2017

From video tutorial here: https://www.youtube.com/watch?v=rraXF0EjRC8

## Random Scatter plot
Ok, lets do another quick interactive example using a scatter plot:

In [16]:
# 1. Data
x = np.random.random(100) # random points betweeon 0-1
y = np.random.random(100) # random points betweeon 0-1

In [17]:
x, y

(array([0.2190384 , 0.58506728, 0.30439843, 0.25132347, 0.11426786,
        0.15130105, 0.73096062, 0.38683252, 0.02324344, 0.80947925,
        0.44597839, 0.76313608, 0.87695479, 0.16619222, 0.20718514,
        0.95454908, 0.3288032 , 0.38960987, 0.09565812, 0.51868858,
        0.39677727, 0.4059086 , 0.63237424, 0.37689126, 0.33033985,
        0.69237995, 0.43150615, 0.99173312, 0.22392179, 0.85227412,
        0.23960465, 0.98803273, 0.09184942, 0.79066729, 0.78272598,
        0.62713226, 0.58173786, 0.95777688, 0.37704654, 0.13824028,
        0.88968559, 0.61068654, 0.09518297, 0.32021056, 0.89734683,
        0.68771414, 0.34255269, 0.02528626, 0.23932992, 0.44647984,
        0.80383412, 0.95389627, 0.55015698, 0.3594936 , 0.98500506,
        0.65123569, 0.72892776, 0.04666025, 0.22309024, 0.86902048,
        0.25695983, 0.45967047, 0.26840798, 0.54786362, 0.58462948,
        0.80002346, 0.25971019, 0.32196763, 0.13661438, 0.04157894,
        0.48587944, 0.12320053, 0.15157322, 0.99

Create scales and axis like we did before:

In [18]:
# 2. scales
x_sc = bqplot.LinearScale()
y_sc = bqplot.LinearScale()

# 3. axis
x_ax = bqplot.Axis(scale = x_sc, label = 'X')
y_ax = bqplot.Axis(scale = y_sc, label = 'Y', orientation = 'vertical')

Create a scatter plot graphing object with these random x/y and scales:

In [19]:
bqplot.Scatter?

In [20]:
# 4. marks
scatters = bqplot.Scatter(x = x,
                          y = y,
                          scales = {'x': x_sc, 'y': y_sc})

Now, lets create a selector to select points along the x-axis.  We will use the `bqplot` interaction called `FastIntervalSelector`:

In [21]:
bqplot.interacts.FastIntervalSelector?

In [22]:
# 5. interactions
selector = bqplot.interacts.FastIntervalSelector(
            scale = x_sc, marks = [scatters]) 

Let's check out the full figure + interaction!

In [23]:
# Finally: fig
fig = bqplot.Figure(marks = [scatters], axes = [x_ax, y_ax], interaction = selector)
fig

Figure(axes=[Axis(label='X', scale=LinearScale(), side='bottom'), Axis(label='Y', orientation='vertical', scal…

This might depend on what computer you are in, but on my mac, I click to start selecting and then double click to "lock in" my selected region.

How do we tell what interval we have selected?

In [24]:
selector.selected

array([0.40826005, 0.78848057])

So, its a little hard to see what points are selected.  There are some hidden tags within our scatter plot points that we can mess with to change our our plot looks.  These have CSS styling (how HTML is styled), so they'll look very un-Pythonic, because they are!  We'll get more into this sort of thing when we are doing Javascript later in the course:

In [25]:
scatters.unselected_style={'opacity': 0.8} # when unselected, make the points a little see-through

scatters.selected_style={'fill': 'red', 'stroke': 'yellow'} # fill with red, outline in yellow when selected

Display updated figure (though, like with widgets, this change is "backreactive" and will show up above as well):

In [26]:
fig = bqplot.Figure(marks = [scatters], axes = [x_ax, y_ax], interaction = selector)
#display(fig)
fig

Figure(axes=[Axis(label='X', scale=LinearScale(), side='bottom'), Axis(label='Y', orientation='vertical', scal…

## Random Heatmap with 2D data

Lets start thinking about heatmaps with some random data:

In [27]:
# 1. Data
data = np.random.random((10, 10))
data # your's may look different!

array([[0.66412624, 0.48249954, 0.43252326, 0.15264388, 0.02535291,
        0.98208301, 0.04035573, 0.78017141, 0.11082985, 0.32040361],
       [0.19738636, 0.14669056, 0.77724321, 0.37191287, 0.58174629,
        0.24159133, 0.90103565, 0.0274849 , 0.04710978, 0.47610691],
       [0.57568683, 0.84949536, 0.01637271, 0.14299782, 0.82834133,
        0.87874142, 0.73004369, 0.57258288, 0.50419256, 0.92087566],
       [0.9064506 , 0.84500285, 0.97617766, 0.08307754, 0.76953203,
        0.84544717, 0.74407192, 0.68134813, 0.76955123, 0.58765208],
       [0.62445237, 0.22417015, 0.83619272, 0.82576979, 0.9972192 ,
        0.65307446, 0.41224198, 0.35340283, 0.87533218, 0.69826387],
       [0.22307114, 0.51421706, 0.27493501, 0.44283929, 0.01220494,
        0.03714786, 0.82686339, 0.98790423, 0.52693336, 0.86462489],
       [0.55439807, 0.66383603, 0.6664908 , 0.92376166, 0.38218217,
        0.79695795, 0.22314905, 0.11392416, 0.72467832, 0.26399282],
       [0.70215128, 0.00919195, 0.1397894

So we just have a 10 x 10 array here.

Lets start by generating a quick heat map with `bqplot`'s `GridHeatMap` marks function. We've been making plots with linear scales before, but now for a heatmap, we will want to make a color scale as well.  Let's start with just assigning a color scale, and going from there:

In [28]:
bqplot.ColorScale?

In [29]:
# 2. Scales -- in this case, just a color scale
col_sc = bqplot.ColorScale() # use bqplot to define a color scale

# 3. Axis -- skipping for now

# 4. Mark -- use colorscale to make make heatmap of our data:
heat_map = bqplot.GridHeatMap(color = data, scales = {'color': col_sc})

# 5. Skipping any interactions

# Finally: figure
fig = bqplot.Figure(marks = [heat_map])
fig

Figure(fig_margin={'top': 60, 'bottom': 60, 'left': 60, 'right': 60}, marks=[GridHeatMap(color=array([[0.66412…

In [30]:
bqplot.GridHeatMap?

There are some things we probably want to do here.  One of them being able to change the color scale -- we spent all this time thinking about color, let's put those thoughts to good use!

In [31]:
# 1. Data -- same as above

# 2. Scale -- color with new color scheme
col_sc = bqplot.ColorScale(scheme = "Reds") # color scheme of reds

# 3. skip Axis

# 4. Marks -- use colorscale to make make heatmap of our data:
heat_map = bqplot.GridHeatMap(color = data, scales = {'color': col_sc})

# Figure
fig = bqplot.Figure(marks = [heat_map])
fig

Figure(fig_margin={'top': 60, 'bottom': 60, 'left': 60, 'right': 60}, marks=[GridHeatMap(color=array([[0.66412…

Let's build upon this plot by adding some axis so that we can think about how to label our data.  Currently, we *only* have a color scale for each color in our 10x10 grid, so we will label this color axis with a colorbar:

In [32]:
bqplot.ColorAxis?

In [33]:
# 1. Data -- same

# 2. Scales -- color
col_sc = bqplot.ColorScale(scheme = "Reds")
# lets plot some axes on our plot as well, in this case
#  our axis will be a color bar, vertically on the right
#  of our heatmap

# 3. Axis (finally) -- here a "color axis" is just a colorbar
c_ax = bqplot.ColorAxis(scale = col_sc, 
                        orientation = 'vertical', 
                        side = 'right') 

# 4. Marks -- put it all together and lets take a look!
heat_map = bqplot.GridHeatMap(color = data, 
                              scales = {'color': col_sc})

# 5. no interactions

# generate fig!
fig = bqplot.Figure(marks = [heat_map], axes = [c_ax])
fig

Figure(axes=[ColorAxis(orientation='vertical', scale=ColorScale(scheme='Reds'), side='right')], fig_margin={'t…

While our x/y bins don't mean anything in particular in this case - we are dealing with just a randomly binned 10x10 dataset after all - we none-the-less probably want to put at least the bin labels on there.  So let's make some x/y scales and some x/y axis (note I'm doing Scales/Axis a bit out of order here to group by kind of axis):

In [34]:
x_sc = bqplot.OrdinalScale()
y_sc = bqplot.OrdinalScale()

x_ax = bqplot.Axis(scale = x_sc)
y_ax = bqplot.Axis(scale = y_sc, 
                   orientation = 'vertical')

Why did I choose ordinal scales?  Well again - the bins, while numbered, don't actually mean anything, so in a sense they are "categorical" bins, and our scales should reflect that fact!

Color scale & color axis like before:

In [35]:
col_sc = bqplot.ColorScale(scheme = "Reds")

c_ax = bqplot.ColorAxis(scale = col_sc, 
                        orientation = 'vertical', 
                        side = 'right')

Combine all these scales, axis and the data into a heat map mark using `bqplot.GridHeatMap`:

In [36]:
# Marks -- lets now re-do our heat map & add in some interactivity:
heat_map = bqplot.GridHeatMap(color = data,
                              scales = {'color': col_sc,
                                        'row': y_sc,
                                        'column': x_sc})

... put these marks and axes on a figure canvas and plot it!

In [37]:
# stir and combine into 1 figure
fig = bqplot.Figure(marks = [heat_map], 
                    axes = [c_ax, y_ax, x_ax])

fig

Figure(axes=[ColorAxis(orientation='vertical', scale=ColorScale(scheme='Reds'), side='right'), Axis(orientatio…

So, we are almost there -- we don't have any interactivity!  Let's get into it.  In this case, we can actually specify the interaction when we are constructing the `GridHeatMap` mark.  Let's do something when we click on each square.  We can do this with a `click-select` interaction.  

In [38]:
# 1. Data -- same

# 2. Scales -- recopy our scales and axis for posterity:
col_sc = bqplot.ColorScale(scheme = "Reds")
x_sc = bqplot.OrdinalScale()
y_sc = bqplot.OrdinalScale()

# 3. Axis -- create axis - for colors, x & y
c_ax = bqplot.ColorAxis(scale = col_sc, 
                        orientation = 'vertical', 
                        side = 'right')
x_ax = bqplot.Axis(scale = x_sc)
y_ax = bqplot.Axis(scale = y_sc, 
                   orientation = 'vertical')

# 4. Marks -- lets now re-do our heat map & add in some interactivity:
heat_map = bqplot.GridHeatMap(color = data,
                              scales = {'color': col_sc,
                                        'row': y_sc,
                                        'column': x_sc},
                              interactions = {'click': 'select'}, # make interactive on click of each box
                              anchor_style = {'fill':'blue'}, # to make our selection blue
                              selected_style = {'opacity': 1.0}, # make 100% opaque if box is selected
                              unselected_style = {'opacity': 0.8}) # make a little see-through if not

# 5. Note: I put interactions in my marks call here!

# stir and combine into 1 figure
fig = bqplot.Figure(marks = [heat_map], 
                    axes = [c_ax, y_ax, x_ax])

fig

Figure(axes=[ColorAxis(orientation='vertical', scale=ColorScale(scheme='Reds'), side='right'), Axis(orientatio…

Ok fine, but our selection isn't linked to anything! Lets check out what heat_map selected actually is before we decide to do something with it:

In [39]:
heat_map.selected
#  note if I select a different box & re-run this cell,
#  I get out different values

So the *trait* of the heat_map that gets updated when we select a box is the x/y indicies.

Let's start simple: write a little function that links the data value to the selected & lets print this in a little ipywidgets label:

In [40]:
mySelectedLabel = ipywidgets.Label()

Let's now define what happens to this label when our heatmap is selected.  If we recall back to when we started learning about ipywidgets and traitlets, this will be a change in the `mySelectedLabel` widget's *value* when a *trait* of our `GridHeatMap` object changes.

First, let's define this action, starting simple: just print out whatever is selected:

In [41]:
def on_selected(change):
    print(change)

Now, let's re-construct our heatmap and link this `on_selected` function to the *trait* of the selected heatmap:

In [42]:
# 1. Data -- same

# 2. Scales -- recopy our scales and axis for posterity:
col_sc = bqplot.ColorScale(scheme = "Reds")
x_sc = bqplot.OrdinalScale()
y_sc = bqplot.OrdinalScale()

# 3. Axis -- create axis - for colors, x & y
c_ax = bqplot.ColorAxis(scale = col_sc, 
                        orientation = 'vertical', 
                        side = 'right')
x_ax = bqplot.Axis(scale = x_sc)
y_ax = bqplot.Axis(scale = y_sc, 
                   orientation = 'vertical')

# 4. Marks -- lets now re-do our heat map & add in some interactivity:
heat_map = bqplot.GridHeatMap(color = data,
                              scales = {'color': col_sc,
                                        'row': y_sc,
                                        'column': x_sc},
                              interactions = {'click': 'select'}, # make interactive on click of each box
                              anchor_style = {'fill':'blue'}, # to make our selection blue
                              selected_style = {'opacity': 1.0}, # make 100% opaque if box is selected
                              unselected_style = {'opacity': 0.8}) # make a little see-through if not

# 5. Note: I put interactions in my marks call here.  BUT now we want to actually DO something with our selection
## THIS IS ALL WE HAVE ADDED!
heat_map.observe(on_selected, 'selected')


# stir and combine into 1 figure
fig = bqplot.Figure(marks = [heat_map], 
                    axes = [c_ax, y_ax, x_ax])

fig

Figure(axes=[ColorAxis(orientation='vertical', scale=ColorScale(scheme='Reds'), side='right'), Axis(orientatio…

So, we can see that what gets printed out when we select is a dictionary -- this is like a "change" dictionary with an ipywidget that we played with last week and it has some familiar things in it like the `old` and `new` keys, the `owner` key, etc.  

Check out the `selected=array...` in the above -- this is how we can grab the index of whatever grid we have selected.

It also is storing a lot of information about our `GridHeatMap` plot!  

Since the change "owner" is our heat_map marks, let's print these out so we can access the indicies.  Once we do this, we can then use these indicies to access the data in our plot.  

One thing at a time though - let's just print out the selected indicies:

In [43]:
def on_selected(change):
    print(change['owner'].selected)

In [44]:
# 1. Data -- same

# 2. Scales -- recopy our scales and axis for posterity:
col_sc = bqplot.ColorScale(scheme = "Reds")
x_sc = bqplot.OrdinalScale()
y_sc = bqplot.OrdinalScale()

# 3. Axis -- create axis - for colors, x & y
c_ax = bqplot.ColorAxis(scale = col_sc, 
                        orientation = 'vertical', 
                        side = 'right')
x_ax = bqplot.Axis(scale = x_sc)
y_ax = bqplot.Axis(scale = y_sc, 
                   orientation = 'vertical')

# 4. Marks -- lets now re-do our heat map & add in some interactivity:
heat_map = bqplot.GridHeatMap(color = data,
                              scales = {'color': col_sc,
                                        'row': y_sc,
                                        'column': x_sc},
                              interactions = {'click': 'select'}, # make interactive on click of each box
                              anchor_style = {'fill':'blue'}, # to make our selection blue
                              selected_style = {'opacity': 1.0}, # make 100% opaque if box is selected
                              unselected_style = {'opacity': 0.8}) # make a little see-through if not

# 5. Note: I put interactions in my marks call here.  BUT now we want to actually DO something with our selection
## THIS IS ALL WE HAVE ADDED!
heat_map.observe(on_selected, 'selected')


# stir and combine into 1 figure
fig = bqplot.Figure(marks = [heat_map], 
                    axes = [c_ax, y_ax, x_ax])

fig

Figure(axes=[ColorAxis(orientation='vertical', scale=ColorScale(scheme='Reds'), side='right'), Axis(orientatio…

It turns out we can actually `SHIFT-select` and select a selection of boxes at one time.  Depending on your browser/OS you can also use `CMD` or `CTRL`-select to select individual boxes.  However, this is a little bit dependent on how your browser/trackpad/mouse is set up.

(`CMD`-select doesn't work in notebooks on my Mac, but it does in jupyter-lab.  Go fig.)

**DEMONSTRATE**

Because of this we actual `selected` set of indicies we want to access can be more than just x/y indicies - it can be an array of indicies representing all of the `SHIFT-select`ed points.

For the sake of simplicity, let's *only* do things when we select one point.  So we will *only* take out the first element of this selected array.  Let's print this with our `on_selected` function:

In [45]:
def on_selected(change):
    if len(change['owner'].selected) == 1:
        print(change['owner'].selected[0])
    # else: don't update anything

In [46]:
# 1. Data -- same

# 2. Scales -- recopy our scales and axis for posterity:
col_sc = bqplot.ColorScale(scheme = "Reds")
x_sc = bqplot.OrdinalScale()
y_sc = bqplot.OrdinalScale()

# 3. Axis -- create axis - for colors, x & y
c_ax = bqplot.ColorAxis(scale = col_sc, 
                        orientation = 'vertical', 
                        side = 'right')
x_ax = bqplot.Axis(scale = x_sc)
y_ax = bqplot.Axis(scale = y_sc, 
                   orientation = 'vertical')

# 4. Marks -- lets now re-do our heat map & add in some interactivity:
heat_map = bqplot.GridHeatMap(color = data,
                              scales = {'color': col_sc,
                                        'row': y_sc,
                                        'column': x_sc},
                              interactions = {'click': 'select'}, # make interactive on click of each box
                              anchor_style = {'fill':'blue'}, # to make our selection blue
                              selected_style = {'opacity': 1.0}, # make 100% opaque if box is selected
                              unselected_style = {'opacity': 0.8}) # make a little see-through if not

# 5. Note: I put interactions in my marks call here.  BUT now we want to actually DO something with our selection
## THIS IS ALL WE HAVE ADDED!
heat_map.observe(on_selected, 'selected')


# stir and combine into 1 figure
fig = bqplot.Figure(marks = [heat_map], 
                    axes = [c_ax, y_ax, x_ax])

fig

Figure(axes=[ColorAxis(orientation='vertical', scale=ColorScale(scheme='Reds'), side='right'), Axis(orientatio…

Now you'll notice if I `SHIFT-select` I still only get the set of x/y indicies associated with the blue selected point.  Sweet.

Now that we have these indicies in our plot, we can (finally) update our Label widget to print out what the data value is at this point:

In [47]:
def on_selected(change):
    if len(change['owner'].selected) == 1: #only 1 selected
        i, j = change['owner'].selected[0] # grab the x/y coordinates
        v = data[i,j] # grab data value
        mySelectedLabel.value = 'Data Value = ' + str(v) # set our label

Now we just have to make sure we show both of the figure and the label when we display:

In [48]:
# 1. Data -- same

# 2. Scales -- recopy our scales and axis for posterity:
col_sc = bqplot.ColorScale(scheme = "Reds")
x_sc = bqplot.OrdinalScale()
y_sc = bqplot.OrdinalScale()

# 3. Axis -- create axis - for colors, x & y
c_ax = bqplot.ColorAxis(scale = col_sc, 
                        orientation = 'vertical', 
                        side = 'right')
x_ax = bqplot.Axis(scale = x_sc)
y_ax = bqplot.Axis(scale = y_sc, 
                   orientation = 'vertical')

# 4. Marks -- lets now re-do our heat map & add in some interactivity:
heat_map = bqplot.GridHeatMap(color = data,
                              scales = {'color': col_sc,
                                        'row': y_sc,
                                        'column': x_sc},
                              interactions = {'click': 'select'}, # make interactive on click of each box
                              anchor_style = {'fill':'blue'}, # to make our selection blue
                              selected_style = {'opacity': 1.0}, # make 100% opaque if box is selected
                              unselected_style = {'opacity': 0.8}) # make a little see-through if not

# 5. Note: I put interactions in my marks call here.  BUT now we want to actually DO something with our selection
## THIS IS ALL WE HAVE ADDED!
heat_map.observe(on_selected, 'selected')


# stir and combine into 1 figure
fig = bqplot.Figure(marks = [heat_map], 
                    axes = [c_ax, y_ax, x_ax])


# ADDED: putting widget and plot together
myDashboard = ipywidgets.VBox([mySelectedLabel, fig]) # have label on top of fig
myDashboard # show

Hey neat!  So now when we do an action, in this case selecting, on one object (the heat map) we have updates *tied to* another object, in this case we are also updating our label widget's value.

This is how we will build up dashboards that allow us to display different aspects of our data in linked views.

Let's practice one of these linked views now by making a linked histogram of a 3D dataset instead of printing the value with a 2D dataset.

## Random heatmap + Histogram with 3D data

Now let's move on to making a preliminary dashboard for multi-dimensional datasets. Let's first start with some randomly generated data again, this time in 3D:

In [49]:
data = np.random.random((10, 10,20))
data

array([[[0.20117314, 0.33354909, 0.10945804, ..., 0.95880471,
         0.12157611, 0.74279734],
        [0.22351515, 0.02501673, 0.58524262, ..., 0.45502543,
         0.4885004 , 0.16323532],
        [0.31833321, 0.09275388, 0.28649964, ..., 0.3799557 ,
         0.45996814, 0.80212751],
        ...,
        [0.8579653 , 0.37049633, 0.03653937, ..., 0.66601038,
         0.21159845, 0.05295993],
        [0.2644555 , 0.90510281, 0.07915774, ..., 0.45189203,
         0.6686609 , 0.75730371],
        [0.77546636, 0.38706262, 0.42875134, ..., 0.0477016 ,
         0.91900612, 0.82859832]],

       [[0.90794893, 0.21171015, 0.89024247, ..., 0.70209318,
         0.3926692 , 0.17451033],
        [0.16400152, 0.74987085, 0.77410344, ..., 0.96721774,
         0.62851563, 0.01800362],
        [0.22279604, 0.92881665, 0.50988623, ..., 0.30340351,
         0.68141243, 0.7054721 ],
        ...,
        [0.68650175, 0.2956913 , 0.44174999, ..., 0.51908975,
         0.88144828, 0.44907433],
        [0.5

In [50]:
data.shape

(10, 10, 20)

In [51]:
data[0,0,:]
# we can see that no instead of 1 value, each "i,j" component
#  has an array of values

array([0.20117314, 0.33354909, 0.10945804, 0.48554365, 0.00830872,
       0.80750939, 0.70719194, 0.72363394, 0.07663447, 0.76927971,
       0.1359332 , 0.62120014, 0.64464403, 0.52468013, 0.88096981,
       0.80954453, 0.3530135 , 0.95880471, 0.12157611, 0.74279734])

Make the heatmap plot like before.

First, scales and axis (x/y and color):

In [52]:
# Scales: now add scales - colors, x & y
col_sc = bqplot.ColorScale(scheme = "Reds")
x_sc = bqplot.OrdinalScale()
y_sc = bqplot.OrdinalScale()

# Axis: create axis - for colors, x & y
c_ax = bqplot.ColorAxis(scale = col_sc, 
                        orientation = 'vertical', 
                        side = 'right')
x_ax = bqplot.Axis(scale = x_sc)
y_ax = bqplot.Axis(scale = y_sc, 
                   orientation = 'vertical')

Now, instead of feeding in `data` like we did in 2D for our heatmap, let's feed in the sum of data along the z-axis:

In [53]:
# Marks: lets now re-do our heat map & add in some interactivity:
heat_map = bqplot.GridHeatMap(color = np.sum(data, axis=2),
                              scales = {'color': col_sc,
                                        'row': y_sc,
                                        'column': x_sc},
                              interactions = {'click': 'select'}, # make interactive on click of each box
                              anchor_style = {'fill':'blue'}, # to make our selection blue
                              selected_style = {'opacity': 1.0}, # make 100% opaque if box is selected
                              unselected_style = {'opacity': 0.8}) # make a little see-through if not

Let's include our label in our dashboard:

In [54]:
# create label again
mySelectedLabel = ipywidgets.Label()

This time, let's have the data print out the sum along the z-axis instead of just a data value at an x/y index position:

In [55]:
def on_selected(change):
    if len(change['owner'].selected) == 1: #only 1 selected
        i, j = change['owner'].selected[0] # grab the x/y coordinates
        v = data[i,j].sum() # grab data value at x/y index and sum along z
        mySelectedLabel.value = 'Data Sum = ' + str(v) # set our label

Observe change:

In [56]:
heat_map.observe(on_selected, 'selected')

Combine and display:

In [57]:
fig = bqplot.Figure(marks = [heat_map], axes = [c_ax, y_ax, x_ax])

myDashboard = ipywidgets.VBox([mySelectedLabel, fig])
myDashboard

Ultimately what we want to do is select an x/y grid and then "expand" our data along z into a histogram such that if we select a grid on our heatmap a new histogram is generated that shows the distribution of values along z.  

Before we link these two things together, let's make a histogram of a single "z" value by fixing our x/y indicies:

In [58]:
i,j = 0,0 # can be any combo

In [59]:
data[i,j] # 20 elements

array([0.20117314, 0.33354909, 0.10945804, 0.48554365, 0.00830872,
       0.80750939, 0.70719194, 0.72363394, 0.07663447, 0.76927971,
       0.1359332 , 0.62120014, 0.64464403, 0.52468013, 0.88096981,
       0.80954453, 0.3530135 , 0.95880471, 0.12157611, 0.74279734])

Let's make a histogram.    

Let's think about what our x/y scales will be: we want to show the distribution of values along z.  Intuitavely, we know this will go between $\sim$0-1 since we have randomly generated values.

So, our "x" axis for this plot should be a linear scale so it can go from 0-1, and our "y" axis should be linear and will show the frequency of values in each bin.

Scales:

In [60]:
x_sch = bqplot.LinearScale()
y_sch = bqplot.LinearScale()

Let's make axis with these scales:

In [61]:
x_axh = bqplot.Axis(scale = x_sch, label = 'Value of 3rd axis')
y_axh = bqplot.Axis(scale = y_sch, 
                    orientation = 'vertical', 
                    label='Frequency')

Now we will use `bqplot.Hist` to make this histogram:

In [62]:
hist = bqplot.Hist(sample = data[i,j,:],
                   normalized = False, # normalized=False means we get counts in each bin
                   scales = {'sample': x_sch, 'count': y_sch}, # sample is data values, count is frequency
                   bins = 5) # number of bins

Note here that we specified this plot in a different way than the `GridHeatMap` and `Scatter` -- each type of `bqplot` plot has different parameters associated with the type of plot we are using.

In [63]:
figh = bqplot.Figure(marks = [hist], axes = [x_axh, y_axh])
figh

Figure(axes=[Axis(label='Value of 3rd axis', scale=LinearScale(), side='bottom'), Axis(label='Frequency', orie…

Let's pause here and think about how to link up our histogram i,j with our selections on the heatmap.  First, what values of the histogram can we update?  Let's check:

In [64]:
hist.keys

['_model_module',
 '_model_module_version',
 '_model_name',
 '_view_count',
 '_view_module',
 '_view_module_version',
 '_view_name',
 'apply_clip',
 'bins',
 'colors',
 'count',
 'display_legend',
 'enable_hover',
 'interactions',
 'labels',
 'midpoints',
 'normalized',
 'opacities',
 'preserve_domain',
 'sample',
 'scales',
 'scales_metadata',
 'selected',
 'selected_style',
 'stroke',
 'tooltip',
 'tooltip_location',
 'tooltip_style',
 'unselected_style',
 'visible']

In [65]:
hist.sample

array([0.20117314, 0.33354909, 0.10945804, 0.48554365, 0.00830872,
       0.80750939, 0.70719194, 0.72363394, 0.07663447, 0.76927971,
       0.1359332 , 0.62120014, 0.64464403, 0.52468013, 0.88096981,
       0.80954453, 0.3530135 , 0.95880471, 0.12157611, 0.74279734])

Hey!  Here is where our data values are stored!  Like with when we observe changes in our heat map and update the values of our ipywidget's value we want to also update this sample's data!  

Let's update our `on_selected` function to reflect this:

In [66]:
def on_selected(change):
    if len(change['owner'].selected) == 1: #only 1 selected
        i, j = change['owner'].selected[0] # grab the x/y coordinates
        v = data[i,j].sum() # grab data value at x/y index and sum along z
        mySelectedLabel.value = 'Data Sum = ' + str(v) # set our label
        # NOW ALSO: update our histogram
        hist.sample = data[i,j,:]

We don't have to go through the exersise of rebuilding our heatmap and histogram in general, but let's just do it for the sake of completeness and not accidentally re-linking thinks we shouldn't:

#1 heatmap:

In [67]:
# (1) Scales: x/y, colors
col_sc = bqplot.ColorScale(scheme = "Reds")
x_sc = bqplot.OrdinalScale()
y_sc = bqplot.OrdinalScale()

# (2) Axis: x/y, colors
c_ax = bqplot.ColorAxis(scale = col_sc, 
                        orientation = 'vertical', 
                        side = 'right')
x_ax = bqplot.Axis(scale = x_sc)
y_ax = bqplot.Axis(scale = y_sc, 
                   orientation = 'vertical')

# (3) Marks: heatmap
heat_map = bqplot.GridHeatMap(color = np.sum(data, axis=2),
                              scales = {'color': col_sc,
                                        'row': y_sc,
                                        'column': x_sc},
                              interactions = {'click': 'select'}, # make interactive on click of each box
                              anchor_style = {'fill':'blue'}, # to make our selection blue
                              selected_style = {'opacity': 1.0}, # make 100% opaque if box is selected
                              unselected_style = {'opacity': 0.8}) # make a little see-through if not

# (4) Link selection on heatmap to other things
heat_map.observe(on_selected, 'selected')

# (5) Paint heatmap canvas, don't display yet:
fig_heatmap = bqplot.Figure(marks = [heat_map], axes = [c_ax, y_ax, x_ax])

#2 histogram:

In [68]:
# (1) scales: x/y, linear
x_sch = bqplot.LinearScale() # range of z-axis data
y_sch = bqplot.LinearScale() # frequency of z-axis data in bins

# (2) axis: x/y
x_axh = bqplot.Axis(scale = x_sch, label = 'Value of 3rd axis')
y_axh = bqplot.Axis(scale = y_sch, 
                    orientation = 'vertical', 
                    label='Frequency')

# (3) Marks: histogram - start with just 0,0 in i/j -- can do other place holders
hist = bqplot.Hist(sample = data[0,0,:],
                   normalized = False, # normalized=False means we get counts in each bin
                   scales = {'sample': x_sch, 'count': y_sch}, # sample is data values, count is frequency
                   bins = 5) # number of bins

# (4) NO LINKING ON HISTOGRAM SIDE

# (5) Paint histogram canvas, don't display yet
fig_hist = bqplot.Figure(marks = [hist], axes = [x_axh, y_axh])

Create dashboard layout and display:

In [69]:
# side by side figures
figures = ipywidgets.HBox([fig_heatmap, fig_hist])

# label on top
myDashboard = ipywidgets.VBox([mySelectedLabel, figures])
myDashboard

Ok close, but its all smooshed!  We can play with the layout of our plots before we display.  To do this we use some more CSS-like styling options, in particular, `layout`:

In [70]:
# mess with figure layout:
fig_heatmap.layout.min_width = '500px' # feel free to change for your screen
fig_hist.layout.min_width = '500px'

# side by side figures
figures = ipywidgets.HBox([fig_heatmap, fig_hist])

# label on top
myDashboard = ipywidgets.VBox([mySelectedLabel, figures])
myDashboard

Note that update was "back-reactive" in that it changed the figure layout above as well!  Super sweet!

#### Further complications: linking in different directions

We can also apply some other links to further enhance our dashboard.  One that we've messed with before is allowing the user to select the number of bins of a histogram.

There are a few ways to do this, but one "easier" way is to just link the histogram "bins" with the value of a bins-slider.  

If we recall: `bins` was another key that was listed in hist:

In [71]:
hist.keys

['_model_module',
 '_model_module_version',
 '_model_name',
 '_view_count',
 '_view_module',
 '_view_module_version',
 '_view_name',
 'apply_clip',
 'bins',
 'colors',
 'count',
 'display_legend',
 'enable_hover',
 'interactions',
 'labels',
 'midpoints',
 'normalized',
 'opacities',
 'preserve_domain',
 'sample',
 'scales',
 'scales_metadata',
 'selected',
 'selected_style',
 'stroke',
 'tooltip',
 'tooltip_location',
 'tooltip_style',
 'unselected_style',
 'visible']

In [72]:
hist.bins = 5 # this changes the bins of our histogram above in a back-reactive way -- traitlets magic!

Let's add a little integer slider to allow our user to select the number of bins for the histogram:

In [73]:
bins_slider = ipywidgets.IntSlider(value=5, min=1, max=data.shape[2]) # don't make more bins than data points!

A reminder of what this looks like:

In [74]:
bins_slider

IntSlider(value=5, max=20, min=1)

We can use `link` or `jslink` to link the value of this slider to our histogram's number of bins:

In [75]:
ipywidgets.jslink((bins_slider, 'value'), (hist, 'bins'))

Link(source=(IntSlider(value=5, max=20, min=1), 'value'), target=(Hist(bins=5, colors=['steelblue'], count=arr…

While this change is "backreactive", let's redo our figure layout so we can see everything a bit better:

In [76]:
# mess with figure layout:
fig_heatmap.layout.min_width = '500px' # feel free to change for your screen
fig_hist.layout.min_width = '500px'

# side by side figures
figures = ipywidgets.HBox([fig_heatmap, fig_hist])

# label on top to the left, bins slider to the right
controls = ipywidgets.HBox([mySelectedLabel, bins_slider])

# combined
myDashboard = ipywidgets.VBox([controls, figures])
myDashboard

## Interactive plots with bqplot's matplotlib-like interface

There is a `matplotlib`-like interface in `bqplot` that we can also use to make interactive figures.

In [77]:
import bqplot.pyplot as bplt

We can start with our gridded heatmap:

In [78]:
# first let's set up a figure object - the call is a little different for bqplot
fig = bplt.figure(padding_y=0.0)

# we'll call plt's gridheatmap function
heat_map = bplt.gridheatmap(data[:,:,0]) # just take bottom part of data
fig

Figure(axes=[ColorAxis(scale=ColorScale()), Axis(orientation='vertical', scale=OrdinalScale(reverse=True)), Ax…

We can make our plots interactive in much the same way as before:

In [79]:
# same function as before:
def on_selected_bplt(change):
    if len(change['owner'].selected) == 1: #only 1 selected
        i, j = change['owner'].selected[0] # grab the x/y coordinates
        v = data[i,j].sum() # grab data value at x/y index and sum along z
        mySelectedLabel.value = 'Data Sum = ' + str(v) # set our label
        # NOW ALSO: update our histogram
        hist.sample = data[i,j,:]

In [80]:
mySelectedLabel = ipywidgets.Label()

In [81]:
fig = bplt.figure(padding_y=0.0) # set up a figure object
bplt.scales(scales={'color':bqplot.ColorScale(scheme='Reds')})

# use bqplot's plt interface to plot:
heat_map = bplt.gridheatmap(np.sum(data, axis=2),
                            interactions={'click':'select'}, 
                            anchor_style = {'fill':'blue'})

# hook heat_maps selected value to the label 
heat_map.observe(on_selected_bplt, 'selected')

# change labels
fig.axes[2].label = 'X' # xaxes label
fig.axes[1].label = 'Y' # yaxes label

# 0 is the colorbar axis
fig.axes[0].orientation = 'horizontal'
fig.axes[0].side = 'top' # vertical and side=right don't work rightnow?

# show both the fig and label in a vertical box
ipywidgets.VBox([mySelectedLabel,fig])

In [82]:
fig_hist = bplt.figure(padding_y=0.0) # set up a figure object

# use bqplot's plt interface to plot:
hist = bplt.hist(sample = data[0,0,:],
                   normalized = False, # normalized=False means we get counts in each bin
                   bins = 5) 

# change labels
fig_hist.axes[1].label = 'Z values' # xaxes label
fig_hist.axes[0].label = 'Frequency' # yaxes label

fig_hist # empty plot of x/y

Figure(axes=[Axis(label='Frequency', orientation='vertical', scale=LinearScale()), Axis(label='Z values', scal…

In [83]:
fig.layout.min_width='500px'
fig_hist.layout.min_width='500px'

ipywidgets.VBox([mySelectedLabel,
                 ipywidgets.HBox([fig,fig_hist])])

## Extras: Interactive histogramming with bqplot

Now, lets try some interactive histogramming of our buildings data:

In [84]:
import pandas as pd
buildings = pd.read_csv("https://uiuc-ischool-dataviz.github.io/is445_AOUAOG_fall2021/week02/data/building_inventory.csv",
                        na_values = {'Year Acquired': 0, 
                                     'Year Constructed': 0, 
                                     'Square Footage': 0})

Let's create some linear scales and attach axis like before:

In [85]:
# since buildings is our data, we don't have to do anything
#  with that, but we do need to create our scales and 
# axes like we've been doing before:
# (1)
x_sc = bqplot.LinearScale()
y_sc = bqplot.LinearScale()
x_ax = bqplot.Axis(scale = x_sc)
y_ax = bqplot.Axis(scale = y_sc, orientation = 'vertical')

# (2) now, lets do an interactive rebinning, but lets
# use bqplot and a slider widget to do it
hist = bqplot.Hist(sample = buildings["Year Acquired"],
            scales = {'sample': x_sc, 'count': y_sc},
                   bins = 128, normalized = True,
                   colors = ["#FFFFFF"])

# lets also create a slider like we've done before
islider = ipywidgets.IntSlider(min = 8, max = 128, step = 1)
# and lets link our sider and our bins of our histogram
ipywidgets.link((islider, 'value'), (hist, 'bins'))
# construct a fig
#fig = bqplot.Figure(marks = [hist], axes = [x_ax, y_ax])
# ***RUN NEXT CELL BEFORE ADDING 2ND HIST

# (3) ok, but maybe we want to see our original histogram
#  underneath, lets add this to our figure
hist2 = bqplot.Hist(sample = buildings["Year Acquired"],
                   opacity = 0.1, normalized = True,
            scales = {'sample': x_sc, 'count': y_sc},
                  bins = 128)
fig = bqplot.Figure(marks = [hist, hist2], axes = [x_ax, y_ax])

# for 2 & 3
#display(ipywidgets.VBox([fig, islider]))
ipywidgets.VBox([fig, islider])

## Extras: Wealth of Nations plot

See full github repo for all of this data/libraries needed!

* originially from the TedTalk: https://www.ted.com/talks/hans_rosling_shows_the_best_stats_you_ve_ever_seen
* found on Rosling's website: https://www.ted.com/talks/hans_rosling_shows_the_best_stats_you_ve_ever_seen
* We're going to make a tool similar to GapMinders:https://www.gapminder.org/world/
* Much of this is, in more detail, in the PyGothum-2017 github: https://github.com/dmadeka/PyGotham-2017 
* This will talk to javascript on the backend to mimic the output of another plotting package d3.js, but we don't have to learn about d3.js (just now) and can instead rely on our current Python knowledge

In [86]:
# import pandas if we have not
import pandas as pd

# lets start off our plot at the initial year of 1800
initial_year = 1800

In [91]:
# we'll read in our datafile and apply 
# some pre-written cleaning routines 
# get out the data we want for our plotting
# put this file in the same directory as the notebook, or link it in your path:
from sys import path
path.append('./library') # this is the subdirectory where wealth_of_nations.py is
from wealth_of_nations import process_data, get_min_max, get_data

# grab data
data = process_data('./library/nations.json')

data

name               region  \
0          Angola   Sub-Saharan Africa   
1           Benin   Sub-Saharan Africa   
2        Botswana   Sub-Saharan Africa   
3    Burkina Faso   Sub-Saharan Africa   
4         Burundi   Sub-Saharan Africa   
..            ...                  ...   
174      Thailand  East Asia & Pacific   
175   Timor-Leste  East Asia & Pacific   
177         Tonga  East Asia & Pacific   
178       Vietnam  East Asia & Pacific   
179       Vanuatu  East Asia & Pacific   

                                                income  \
0    [359.93, 359.93, 359.93, 359.93, 359.93, 359.9...   
1    [553.72, 553.72, 553.72, 553.72, 553.72, 553.7...   
2    [407.36, 407.36, 407.36, 407.36, 407.36, 407.3...   
3    [454.33, 454.33, 454.33, 454.33, 454.33, 454.3...   
4    [447.59, 447.59, 447.59, 447.59, 447.59, 447.5...   
..                                                 ...   
174  [496.98, 496.98, 496.98, 496.98, 496.98, 496.9...   
175  [514.12, 514.3505, 514.581, 514.8115, 515.042,...   
177  [667.71, 667.71, 667.71, 667.71, 667.71, 667.7...   
178  [459.71, 459.71, 459.71, 459.71, 459.71, 459.7...   
179  [829.58, 829.58, 829.58, 829.58, 829.58, 829.5...   

                                            population  \
0    [1567028.0, 1567028.0, 1567028.0, 1567028.0, 1...   
1    [636559.0, 636559.0, 636559.0, 636559.0, 63655...   
2    [121000.0, 121000.0, 121000.0, 121000.0, 12100...   
3    [1665421.0, 1665421.0, 1665421.0, 1665421.0, 1...   
4    [899097.0, 899097.0, 899097.0, 899097.0, 89909...   
..                                                 ...   
174  [4665000.0, 4665000.0, 4665000.0, 4665000.0, 4...   
175  [137262.0, 137262.0, 137262.0, 137262.0, 13726...   
177  [18658.0, 18654.325581395347, 18650.6511627907...   
178  [6551000.0, 6551000.0, 6551000.0, 6551000.0, 6...   
179  [27791.0, 27791.0, 27791.0, 27791.0, 27791.0, ...   

                                        lifeExpectancy  
0    [26.98, 26.98, 26.98, 26.98, 26.98, 26.98, 26....  
1    [31.0, 31.0, 31.0, 31.0, 31.0, 31.0, 31.0, 31....  
2    [33.6, 33.6, 33.6, 33.6, 33.6, 33.6, 33.6, 33....  
3    [29.2, 29.2, 29.2, 29.2, 29.2, 29.2, 29.2, 29....  
4    [31.5, 31.5, 31.5, 31.5, 31.5, 31.5, 31.5, 31....  
..                                                 ...  
174  [30.4, 30.4, 30.4, 30.4, 30.4, 30.4, 30.4, 30....  
175  [28.97, 28.97, 28.97, 28.97, 28.97, 28.97, 28....  
177  [57.91, 57.91, 57.91, 57.91, 57.91, 57.91, 57....  
178  [32.0, 32.0, 32.0, 32.0, 32.0, 32.0, 32.0, 32....  
179  [40.8, 40.8, 40.8, 40.8, 40.8, 40.8, 40.8, 40....  

[178 rows x 5 columns]

In [92]:
# grab min & max values of our variables of interest
income_min, income_max, life_exp_min, life_exp_max, pop_min, pop_max = get_min_max(data)

In [93]:
# lets allow for a mouse-over interaction
# for silly:
import bqplot
tt = bqplot.Tooltip(fields=['name', 'x', 'y'], 
                    labels=['Country Name', 
                            'Income per Capita', 'Life Expectancy'])
#bqplot.Tooltip?

In [94]:
# we will label what year is being plotted, just like in the Gabminder plot
year_label = bqplot.Label(x=[0.75], y=[0.10], 
                   font_size=52, font_weight='bolder', 
                   colors=['orange'],
                   text=[str(initial_year)], enable_move=True)

In [95]:
# we'll define our scales like before
# here we scale our x & y axis to the scales of the min and max of our data
x_sc = bqplot.LogScale(min=income_min, max=income_max)
y_sc = bqplot.LinearScale(min=life_exp_min, max=life_exp_max)

# this is just something to color-code each circle by the region it corresponds to
#  (for example, asia, south america, africa, etc)
# the colors call is just mapping each catagorical variable to a color
c_sc = bqplot.OrdinalColorScale(domain=data['region'].unique().tolist(), 
                                colors=bqplot.CATEGORY10[:6])

# finally, we want the size of each of our dots to correspond to the population of 
# each country
#size_sc = bqplot.LinearScale(min=pop_min, max=pop_max)#, mid_range=0.1)
size_sc = bqplot.LinearScale(max=1326856173.0, min=2128.0)
#bqplot.LinearScale?

In [96]:
# create and label our x & y axis
ax_y = bqplot.Axis(label='Life Expectancy', scale=y_sc, 
                   orientation='vertical', side='left', 
                   grid_lines='solid')
ax_x = bqplot.Axis(label='Income per Capita', scale=x_sc, 
                   grid_lines='solid')

In [97]:
# now we'll use another little function from our library above to grab
# data for our initial setup (year = 1800)
# Start with the first year's data
cap_income, life_exp, pop = get_data(data,initial_year,initial_year)

In [98]:
# now lets make our scatter plot!
wealth_scat = bqplot.Scatter(x=cap_income, y=life_exp, 
                             color=data['region'], size=pop,
                      names=data['name'], display_names=False,
                      scales={'x': x_sc, 'y': y_sc, 'color': c_sc, 
                              'size': size_sc},
                      default_size=4112, tooltip=tt, 
                             animate=True, stroke='Black',
                      unhovered_style={'opacity': 0.5})
# much of these calls are things we've seen before, others will allow fun things 
#  like animation and also the ability to click on our plot and interact with it

In [99]:
# for our initial, 1800 view, we'll just allow the first "line" of the evolution of the 
# each nation's track to be displayed... this is essentially a place holder (visible = false)
nation_line = bqplot.Lines(x=data['income'][0], 
                           y=data['lifeExpectancy'][0], 
                           colors=['Gray'],
                       scales={'x': x_sc, 'y': y_sc}, visible=False)

In [100]:
# milliseconds of time between changes we make
time_interval = 10

In [101]:
# create the figure & 
fig = bqplot.Figure(marks=[wealth_scat, year_label, nation_line], 
                    axes=[ax_x, ax_y],
             title='Health and Wealth of Nations', 
                    animation_duration=time_interval)

# lets control the size in pixels too
fig.layout.min_width = '960px'
fig.layout.min_height = '640px'

In [102]:
# we'll use our friend the int slider to slide through years
# for silly:
import ipywidgets
year_slider = ipywidgets.IntSlider(min=1800, max=2008, step=1, description='Year', value=initial_year)

In [103]:
# make sure we define what happens when we change the year on our slider
def year_changed(change):
    wealth_scat.x, wealth_scat.y, wealth_scat.size = get_data(data,year_slider.value,initial_year)
    #wealth_scat.size+=1000
    year_label.text = [str(year_slider.value)]

year_slider.observe(year_changed, 'value')

In [104]:
# now we'll say what happens when we hover over an object
# we'll use "change" again to make it such that if a 
# user hovers over a country, the countries "life line" 
#  is visible
def hover_changed(change):
    if change.new is not None:
        nation_line.x = data['income'][change.new + 1]
        nation_line.y = data['lifeExpectancy'][change.new + 1]
        nation_line.visible = True
    else:
        nation_line.visible = False
        
wealth_scat.observe(hover_changed, 'hovered_point')

In [105]:
# finally, lets add a little play button so we can animate
#  what happens in time, just like on the d3.js plot
play_button = ipywidgets.Play(min=1800, max=2008, interval=time_interval)
# note, we use "jslink" because the "backend" here is javascript
#  bqplot is just interacting with javascript
ipywidgets.jslink((play_button, 'value'), (year_slider, 'value'))

Link(source=(Play(value=1800, interval=10, max=2008, min=1800), 'value'), target=(IntSlider(value=1800, descri…

In [106]:
# finally, lets put it all together!!

ipywidgets.VBox([ipywidgets.HBox([play_button, year_slider]), fig])